In [2]:
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
import helper.flowtracing as ft
import helper.entsoe_wrapper as entsoe_wrapper
from entsoe import EntsoePandasClient
import helper.capacity as cap
from tqdm import tqdm

### Setup the Tracing

- 27 European Countries with Generation, Load, Import and Export
- Entsoe Client is used to load the data for the Generation and Load


#### ToDo

- Setup storage usage
- Check Load and external imports and exports

In [3]:
# Define the start and end dates in UTC
start_utc = pd.Timestamp('2022-01-01', tz='UTC')
end_utc = pd.Timestamp('2023-01-01', tz='UTC')
server_countries=["DE","AT","PL","FR","IT","ES","SE","NL","BE"]
# Codes for the Countries in the List
countryCodes=["AT","PT","ES","FR","IT","GR","ME","BG","RO","RS","HU","SK","SI","CZ","BE","NL","EE","LV","LT","FI","NO","SE","DK","PL","DE","IE"]

In [4]:
#   Load data
gen_dict,gen_types=entsoe_wrapper.get_generation_dict(countryCodes,start_utc,end_utc,imputation_type="no")
gen_types.difference_update(["Hydro Pumped Storage_Actual Consumption"])
import_dict=entsoe_wrapper.get_import_dict(countryCodes,start_utc,end_utc,imputation_type="no") 
export_dict=entsoe_wrapper.get_export_dict(countryCodes,start_utc,end_utc,imputation_type="no")

### Calculation

In [46]:
from concurrent.futures import ThreadPoolExecutor

def solve_linear_system(A, b):
    """
    Solve the linear system Ax = b for a single timestep.
    """
    try:
        return np.linalg.solve(A, b)
    except np.linalg.LinAlgError:
        return np.full(b.shape, np.nan)  # Return NaNs if the system is singular

def solve_linear_systems_parallel(A, b, valid_countries_list, n_countries):
    """
    Solve the linear systems Ax = b in parallel for all timesteps, adjusting for NaN values.

    Parameters:
    - A: list of numpy arrays of shape (n, n)
    - b: list of numpy arrays of shape (n,)
    - valid_countries_list: list of lists containing valid country indices for each timestep
    - n_countries: total number of countries

    Returns:
    - x: numpy array of shape (timesteps, n) containing the solutions
    """
    timesteps = len(A)
    
    # Initialize the result array
    x = np.full((timesteps, n_countries), np.nan)
    
    # Use ThreadPoolExecutor to parallelize the computation
    with ThreadPoolExecutor() as executor:
        results = list(executor.map(solve_linear_system, A, b))
    
    # Collect the results
    for t, result in enumerate(results):
        x[t, valid_countries_list[t]] = result
    
    return x

In [47]:
netimp_dict={}
for country_code in countryCodes:
    netimp_dict[country_code]=export_dict[country_code]-import_dict[country_code]

In [87]:
# Scale the generation based on imports from other countries
def scale_generation(gen_dict, import_dict, countries):
    scaled_gen_dict ={}
    # Calculate the total import from countries not included in the topology
    for country_code in countries:
            # total import from countries not included in the topology
            sum=0
            for country in import_dict[country_code].keys():
                  if country not in countries:
                        sum+=import_dict[country_code][country].iloc[0]          
            scaled_gen_dict[country_code] = gen_dict[country_code].iloc[0] * (1 + sum / gen_dict[country_code].iloc[0].sum())
    return scaled_gen_dict
scaled_gen_dict=scale_generation(gen_dict, import_dict, countrycodes_new)

In [6]:
gen_dict_without_con=gen_dict.copy()
for country in countryCodes:
    gen_dict_without_con[country] = gen_dict[country].loc[:, ~gen_dict[country].columns.str.contains("Actual Consumption")]

In [49]:
def get_b(gen_type, countryCodes, timesteps):
    b = np.array([gen_dict[country_code][gen_type].iloc[:timesteps].values for country_code in countryCodes]).T
    return b

def get_A(countrycodes_new, timesteps):
    n = len(countrycodes_new)
    A = np.zeros((timesteps, n, n))
    
    for i, country_code in enumerate(countrycodes_new):
        A[:, i, i] = gen_dict_without_con[country_code].sum(axis=1).iloc[:timesteps].values
        for key in netimp_dict[country_code].columns:
            if key in countrycodes_new:
                A[:, i, i] -= netimp_dict[country_code][key].iloc[:timesteps].values
        
        for s, country_code2 in enumerate(countrycodes_new):
            if i != s:
                A[:, i, s] = netimp_dict[country_code].get(country_code2, pd.Series([0])).iloc[:timesteps].values
    
    return A

def adjust_for_nan(A, b, countryCodes):
    """
    Adjust the matrix A and vector b to exclude countries with NaN values at specific timesteps.
    """
    n_timesteps, n_countries, _ = A.shape
    
    A_new = []
    b_new = []
    valid_countries_list = []
    
    for t in range(n_timesteps):
        nan_countries = []
        
        # Identify countries with NaN values at this timestep in `b` or diagonal of `A`
        for i, country_code in enumerate(countryCodes):
            if np.isnan(b[t, i]) or np.isnan(A[t, i, i]):
                nan_countries.append(i)
        
        # Exclude contributions for identified NaN countries
        valid_countries = [i for i in range(n_countries) if i not in nan_countries]
        valid_countries_list.append(valid_countries)
        
        A_new.append(A[t, valid_countries, :][:, valid_countries])
        b_new.append(b[t, valid_countries])
    return A_new, b_new, valid_countries_list
    
timesteps=8761
A = get_A(countryCodes, timesteps)
q = {}
# Apply the adjustment
for gen_type in gen_types:
    b = get_b(gen_type, countryCodes, timesteps)
    A_adjusted, b_adjusted, valid_countries_list = adjust_for_nan(A.copy(), b.copy(), countryCodes)
    q[gen_type] = solve_linear_systems_parallel(A_adjusted, b_adjusted, valid_countries_list, len(countryCodes))

In [50]:
q

{'Fossil Oil': array([[ 0.00052743,  0.00182989,  0.00575312, ...,  0.01913026,
          0.0055554 ,  0.        ],
        [ 0.00056301,  0.00220424,  0.00562623, ...,  0.01862607,
          0.0057983 ,  0.        ],
        [ 0.00126409,  0.00230798,  0.00541855, ...,  0.01944491,
          0.00590273,  0.        ],
        ...,
        [ 0.00019954, -0.00085038,  0.0015203 , ...,  0.02304216,
          0.00586526,  0.08456973],
        [ 0.00235943,         nan,         nan, ...,         nan,
          0.00754964,  0.09309866],
        [ 0.00309371, -0.00061216,  0.00216956, ...,  0.02562578,
          0.00610968,  0.09761905]], shape=(8761, 26)),
 'Geothermal': array([[ 3.52426877e-04, -5.41050545e-05, -1.70104734e-04, ...,
          2.35997833e-05,  5.62578733e-04,  0.00000000e+00],
        [-3.75126909e-06, -5.82489154e-05, -1.48678112e-04, ...,
          1.96703167e-05,  6.01005015e-04,  0.00000000e+00],
        [ 1.60929433e-03, -6.01048861e-05, -1.41111111e-04, ...,
          

In [51]:
sum=0
for gen_type in gen_types:
    q[gen_type]=np.nan_to_num(q[gen_type],0)
    sum+=q[gen_type]

In [54]:
np.max(sum)

np.float64(112.17485009643615)

In [55]:
sum

array([[1.        , 1.        , 1.        , ..., 1.        , 1.        ,
        1.        ],
       [1.        , 1.        , 1.        , ..., 1.        , 1.        ,
        1.        ],
       [1.        , 1.        , 1.        , ..., 1.        , 1.        ,
        1.        ],
       ...,
       [0.99997197, 0.99999965, 1.00000063, ..., 1.00000115, 1.00000064,
        1.        ],
       [0.82892003, 0.        , 0.        , ..., 0.        , 1.15765967,
        1.        ],
       [1.00007198, 0.99999993, 1.00000025, ..., 1.00001029, 0.99999404,
        1.        ]], shape=(8761, 26))

In [176]:
missing_data_dict = {}
for country_code in countryCodes:
    missing_data_dict[country_code] = (gen_dict[country_code].isna().sum(axis=1) > 0) | (import_dict[country_code].isna().sum(axis=1) > 0) | (export_dict[country_code].isna().sum(axis=1) > 0)


In [192]:
# Convert the dictionary of pandas series to a numpy array
missing_data_array = np.array([missing_data_dict[country].values for country in countryCodes])

# Check the shape of the resulting array
print(missing_data_array.shape)

(26, 8761)


In [56]:
import plotly.graph_objects as go

# Create the heatmap
fig = go.Figure(data=go.Heatmap(
    z=sum.T,
    x=np.arange(sum.shape[0]),
    y=countryCodes,
    colorscale='Viridis',  # Use a continuous colorscale
    colorbar=dict(title='Numeric Value')
))

# Update layout
fig.update_layout(
    title='Numeric Heatmap',
    xaxis_title='Hour',
    yaxis_title='Country',
    yaxis=dict(tickmode='array', tickvals=np.arange(len(countryCodes)), ticktext=countryCodes)
)

# Show the plot
fig.show()